In [1]:
# --- core ---
import os
import asyncio
import datetime as dt
from zoneinfo import ZoneInfo
import nest_asyncio
import math
nest_asyncio.apply()   # only needed if running in Jupyter

# --- alpaca trading / data ---
from alpaca.data.timeframe import TimeFrame
from alpaca.trading.client import TradingClient
from alpaca.trading.requests import MarketOrderRequest, StopOrderRequest
from alpaca.trading.enums import OrderSide, TimeInForce
from alpaca.data.historical import StockHistoricalDataClient
from alpaca.data.requests import StockBarsRequest, StockLatestTradeRequest
from alpaca.data.live import StockDataStream
from alpaca.data.enums import DataFeed


# --- optional (only if you want data analysis or plotting) ---
# import pandas as pd
# import numpy as np
# import matplotlib.pyplot as plt
# import yfinance as yf
# import backtrader as bt
# import pytz
#api_key="PKB9SXQSORHZSB1VIXY0"
#secret_key="q4n01bamgGErL7p261A7mu5UvHZOOTO2i6rSsXgJ"



In [2]:
# latest code should work fine - test on 08/19 

API_KEY    = "PKB9SXQSORHZSB1VIXY0"
API_SECRET = "q4n01bamgGErL7p261A7mu5UvHZOOTO2i6rSsXgJ"

trading = TradingClient(API_KEY, API_SECRET, paper=True)
client = StockHistoricalDataClient(API_KEY, API_SECRET)

symbol = "PRFX"

# look back a week to be safe
start = dt.datetime.utcnow() - dt.timedelta(days=7)

req = StockBarsRequest(
    symbol_or_symbols=symbol,
    timeframe=TimeFrame.Day,
    start=start,
)

bars = client.get_stock_bars(req).df

# If multiple days, take the second-to-last bar = yesterday's close
bars = bars.xs(symbol, level="symbol") if "symbol" in bars.index.names else bars
bars = bars.sort_index()

if len(bars) >= 2:
    prior_close = float(bars["close"].iloc[-2])
    prior_ts    = bars.index[-2] 
else:
    prior_close = float(bars["close"].iloc[-1])
    prior_ts    = bars.index[-1] 

print(f"Yesterday's close for {symbol}: {prior_close} @ {prior_ts}")
#print(bars)

state = {
    "activated": False,
    "shares": 0,         # negative = short
    "proceeds": 0.0,     # sum(|qty| * price) for shorts
    "mwap": 0.0,         # proceeds / |shares|
}

activated = False
stream = StockDataStream(API_KEY, API_SECRET, feed=DataFeed.IEX)  # or SIP if you have subscription


async def on_trade(trade):
    print("TICK!")
    if trade.symbol != symbol:
        return

    price = float(trade.price)
    ts    = trade.timestamp
    print(f"Live tick: {trade.symbol} {price} at {ts}")

    # 1) Trigger
    if (not state["activated"]) and (price / prior_close) >= 1.5:  # 5% above prior close
        state["activated"] = True

        init_qty = 100                     # initial short (shares)
        # place initial short (SELL init_qty)
        order = trading.submit_order(MarketOrderRequest(
            symbol=symbol,
            qty=init_qty,
            side=OrderSide.BUY,
            time_in_force=TimeInForce.DAY
        ))

        #market_order = trading.submit_order(order_data=order)


        # update short state: shares negative
        state["shares"]   += init_qty
        state["proceeds"] += init_qty * price
        q = abs(state["shares"])
        state["mwap"]     = state["proceeds"] / q
        print(f"[ENTER] long {init_qty} @ ~{price:.4f} | pos={state['shares']} | MWAP={state['mwap']:.4f}")

        return  # done on this tick

    # 2) Ladder adds (only after activated and already short)
    if state["activated"] and state["shares"] > 0:
        target = 0.9 * price
        M = state["mwap"]
        if M < 3.0:  # don't ladder if MWAP is too low
            # dq = q*(T - M) / (P - T)  ; add_shares = int(dq) >= 1
            q = abs(state["shares"])
            if price > target:  # guard divide by zero
                dq = (q * (target - M)) / (price - target)
                add = max(1, int(math.floor(dq)))  # integer shares to ADD
                # submit ONLY the delta
                order = trading.submit_order(MarketOrderRequest(
                    symbol=symbol,
                    qty=add,
                    side=OrderSide.BUY,
                    time_in_force=TimeInForce.DAY
                ))
                # update state
                state["shares"]   += add
                state["proceeds"] += add * price
                state["mwap"]      = state["proceeds"] / abs(state["shares"])
                print(f"[LADDER] add {add} @ ~{price:.4f} | pos={state['shares']} | MWAP={state['mwap']:.4f}")

    if state["activated"] and state["shares"] > 0:
        # 3) Stop loss
        if price <= 0.9 * state["mwap"]:
            order = trading.submit_order(MarketOrderRequest(
                symbol=symbol,
                qty=abs(state["shares"]),
                side=OrderSide.SELL,
                time_in_force=TimeInForce.DAY
            ))
            print(f"[EXIT] stop loss @ ~{price:.4f} | pos={state['shares']} | MWAP={state['mwap']:.4f}")    

stream.subscribe_trades(on_trade, symbol)

# run
import asyncio
asyncio.run(stream._run_forever())

C:\Users\YOGA\AppData\Local\Temp\ipykernel_4004\2289369349.py:12: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  start = dt.datetime.utcnow() - dt.timedelta(days=7)


Yesterday's close for PRFX: 1.34 @ 2025-08-18 04:00:00+00:00
TICK!
Live tick: PRFX 2.32 at 2025-08-19 18:52:50.849922+00:00
[ENTER] long 100 @ ~2.3200 | pos=100 | MWAP=2.3200
TICK!
Live tick: PRFX 2.32 at 2025-08-19 18:52:57.274880+00:00
[LADDER] add 1 @ ~2.3200 | pos=101 | MWAP=2.3200
TICK!
Live tick: PRFX 2.3 at 2025-08-19 18:54:55.477397+00:00
[LADDER] add 1 @ ~2.3000 | pos=102 | MWAP=2.3198
TICK!
Live tick: PRFX 2.29 at 2025-08-19 18:55:29.268789+00:00
[LADDER] add 1 @ ~2.2900 | pos=103 | MWAP=2.3195
TICK!
Live tick: PRFX 2.28 at 2025-08-19 18:56:02.271270+00:00
[LADDER] add 1 @ ~2.2800 | pos=104 | MWAP=2.3191
TICK!
Live tick: PRFX 2.3 at 2025-08-19 18:56:26.089240+00:00
[LADDER] add 1 @ ~2.3000 | pos=105 | MWAP=2.3190


data websocket error, restarting connection: no close frame received or sent
error during websocket communication: [Errno 11001] getaddrinfo failed
Traceback (most recent call last):
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\alpaca\data\live\websocket.py", line 343, in _run_forever
    await self._start_ws()
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\alpaca\data\live\websocket.py", line 134, in _start_ws
    await self._connect()
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\alpaca\data\live\websocket.py", line 98, in _connect
    self._ws = await websockets_legacy.connect(
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFound

TICK!
Live tick: PRFX 2.33 at 2025-08-19 19:32:25.836627+00:00
[LADDER] add 1 @ ~2.3300 | pos=106 | MWAP=2.3191
TICK!
Live tick: PRFX 2.33 at 2025-08-19 19:32:26.296064+00:00
[LADDER] add 1 @ ~2.3300 | pos=107 | MWAP=2.3192
TICK!
Live tick: PRFX 2.33 at 2025-08-19 19:32:39.049807+00:00
[LADDER] add 1 @ ~2.3300 | pos=108 | MWAP=2.3193
TICK!
Live tick: PRFX 2.32 at 2025-08-19 19:32:43.630473+00:00
[LADDER] add 1 @ ~2.3200 | pos=109 | MWAP=2.3193
TICK!
Live tick: PRFX 2.31 at 2025-08-19 19:32:43.639046+00:00
[LADDER] add 1 @ ~2.3100 | pos=110 | MWAP=2.3192
TICK!
Live tick: PRFX 2.32 at 2025-08-19 19:33:10.733001+00:00
[LADDER] add 1 @ ~2.3200 | pos=111 | MWAP=2.3192
TICK!
Live tick: PRFX 2.3 at 2025-08-19 19:33:42.764356+00:00
[LADDER] add 1 @ ~2.3000 | pos=112 | MWAP=2.3190
TICK!
Live tick: PRFX 2.31 at 2025-08-19 19:33:48.032339+00:00
[LADDER] add 1 @ ~2.3100 | pos=113 | MWAP=2.3189
TICK!
Live tick: PRFX 2.32 at 2025-08-19 19:33:48.896965+00:00
[LADDER] add 1 @ ~2.3200 | pos=114 | MWAP=

data websocket error, restarting connection: no close frame received or sent


...

TICK!
Live tick: PRFX 2.45 at 2025-08-19 20:36:56.735024+00:00


error during websocket communication: {"code":40310000,"existing_order_id":"895a8657-0858-4b82-a14e-52f15b3be78e","message":"potential wash trade detected. use complex orders","reject_reason":"opposite side market/stop order exists"}
Traceback (most recent call last):
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\alpaca\common\rest.py", line 198, in _one_request
    response.raise_for_status()
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\requests\models.py", line 1026, in raise_for_status
    raise HTTPError(http_error_msg, response=self)
requests.exceptions.HTTPError: 403 Client Error: Forbidden for url: https://paper-api.alpaca.markets/v2/orders

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "C:\Users\YOGA\AppData\Local\Pa

TICK!
Live tick: PRFX 2.45 at 2025-08-19 20:37:24.816360+00:00


data websocket error, restarting connection: no close frame received or sent
error during websocket communication: [Errno 11001] getaddrinfo failed
Traceback (most recent call last):
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\alpaca\data\live\websocket.py", line 343, in _run_forever
    await self._start_ws()
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\alpaca\data\live\websocket.py", line 134, in _start_ws
    await self._connect()
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\alpaca\data\live\websocket.py", line 98, in _connect
    self._ws = await websockets_legacy.connect(
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\YOGA\AppData\Local\Packages\PythonSoftwareFound

KeyboardInterrupt: 

In [ ]:
await stream.stop()
await stream_task
print("Stream stopped.")